# 은행 데이터 세트를 사용한 이진 분류

*실제 분석과정에서 여러 시행착오가 있었지만, 최종 결과만 기록하였다

In [2]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

## 1.전처리

In [3]:
 train = pd.read_csv('../input/playground-series-s5e8/train.csv')
 test = pd.read_csv('../input/playground-series-s5e8/test.csv')

In [4]:
#데이터셋 정보 출력
print(train.info())
print(test.info())
print(train.shape)
print(test.shape)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 750000 entries, 0 to 749999
Data columns (total 18 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   id         750000 non-null  int64 
 1   age        750000 non-null  int64 
 2   job        750000 non-null  object
 3   marital    750000 non-null  object
 4   education  750000 non-null  object
 5   default    750000 non-null  object
 6   balance    750000 non-null  int64 
 7   housing    750000 non-null  object
 8   loan       750000 non-null  object
 9   contact    750000 non-null  object
 10  day        750000 non-null  int64 
 11  month      750000 non-null  object
 12  duration   750000 non-null  int64 
 13  campaign   750000 non-null  int64 
 14  pdays      750000 non-null  int64 
 15  previous   750000 non-null  int64 
 16  poutcome   750000 non-null  object
 17  y          750000 non-null  int64 
dtypes: int64(9), object(9)
memory usage: 103.0+ MB
None
<class 'pandas.core.frame.DataFr

In [5]:
#타겟 데이터 분리하기
#참고:duration은 현실 문제에선 적용할 수 없음
train_data = train.drop(['id', 'y'],axis=1 )#'poutcome', 'pdays', 'day', 'month', 'duration'
train_target = train['y']
test_data = test.drop(['id'], axis=1 )
print(train_data.shape)
print(train_target.shape)
print(test_data.shape)

(750000, 16)
(750000,)
(250000, 16)


In [6]:
train_data.describe()

age        balance            day       duration  \
count  750000.000000  750000.000000  750000.000000  750000.000000   
mean       40.926395    1204.067397      16.117209     256.229144   
std        10.098829    2836.096759       8.250832     272.555662   
min        18.000000   -8019.000000       1.000000       1.000000   
25%        33.000000       0.000000       9.000000      91.000000   
50%        39.000000     634.000000      17.000000     133.000000   
75%        48.000000    1390.000000      21.000000     361.000000   
max        95.000000   99717.000000      31.000000    4918.000000   

            campaign          pdays       previous  
count  750000.000000  750000.000000  750000.000000  
mean        2.577008      22.412733       0.298545  
std         2.718514      77.319998       1.335926  
min         1.000000      -1.000000       0.000000  
25%         1.000000      -1.000000       0.000000  
50%         2.000000      -1.000000       0.000000  
75%         3.000000      -1.000000       0.000000  
max        63.000000     871.000000     200.000000

In [30]:
#추가 pandas_profiling를 통한 데이터셋 자동 분석
import pandas_profiling
report = pd.DataFrame(train_data).profile_report()
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 59/59 [00:13<00:00,  4.32it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
#특성 별 타깃비율 확인
for c in ['job','marital','education', 'default','loan', 'contact', 'housing','poutcome','month']:
    print(c, '\n', pd.crosstab(train[c], train['y'], normalize='index'))

job 
 y                     0         1
job                              
admin.         0.883547  0.116453
blue-collar    0.932562  0.067438
entrepreneur   0.918614  0.081386
housemaid      0.915347  0.084653
management     0.849608  0.150392
retired        0.753759  0.246241
self-employed  0.870557  0.129443
services       0.917286  0.082714
student        0.659216  0.340784
technician     0.881679  0.118321
unemployed     0.820177  0.179823
unknown        0.879328  0.120672
marital 
 y                0         1
marital                     
divorced  0.888424  0.111576
married   0.898128  0.101872
single    0.829547  0.170453
education 
 y                 0         1
education                    
primary    0.916903  0.083097
secondary  0.894509  0.105491
tertiary   0.837351  0.162649
unknown    0.866613  0.133387
default 
 y               0         1
default                    
no       0.878053  0.121947
yes      0.953693  0.046307
loan 
 y            0         1
loan             

In [8]:
print(train.loc[train['y']==1, 'duration'].describe())

count    90488.000000
mean       638.327226
std        353.249625
min          1.000000
25%        358.000000
50%        609.000000
75%        855.000000
max       4918.000000
Name: duration, dtype: float64


## 2. 피쳐 엔지니어링

In [10]:
#EDA 결과를 고려하여 피쳐 조합,생성
train_data['duration500up'] = (train_data['duration'] >= 500).astype(int)
train_data['duration'] = np.log1p(train_data['duration'])
train_data['balance'] = np.log1p(train_data['balance'].apply(lambda x: x + 8020))
train_data['student_default'] = ((train_data['job'] == 'student') & (train_data['default'] == 'no')).astype(int)
train_data['student_loan'] = ((train_data['job'] == 'student') & (train_data['loan'] == 'no')).astype(int)
train_data['student_housing'] = ((train_data['job'] == 'student') & (train_data['housing'] == 'no')).astype(int)
train_data['retired_single'] = ((train_data['job'] == 'retired') & (train_data['marital'] == 'single')).astype(int)
train_data['retired_loan'] = ((train_data['job'] == 'retired') & (train_data['loan'] == 'no')).astype(int)
train_data['single_tertiary'] = ((train_data['marital'] == 'single') & (train_data['education'] == 'tertiary')).astype(int)
train_data['single_default'] = ((train_data['marital'] == 'single') & (train_data['default'] == 'no')).astype(int)
train_data['single_loan'] = ((train_data['marital'] == 'single') & (train_data['loan'] == 'no')).astype(int)
train_data['single_housing'] = ((train_data['marital'] == 'single') & (train_data['housing'] == 'no')).astype(int)
train_data['tertiary_default'] = ((train_data['education'] == 'tertiary') & (train_data['default'] == 'no')).astype(int)
train_data['tertiary_loan'] = ((train_data['education'] == 'tertiary') & (train_data['loan'] == 'no')).astype(int)
train_data['tertiary_housing'] = ((train_data['education'] == 'tertiary') & (train_data['housing'] == 'no')).astype(int)
train_data['default_loan'] = ((train_data['default'] == 'no') & (train_data['loan'] == 'no')).astype(int)
train_data['default_housing'] = ((train_data['default'] == 'no') & (train_data['housing'] == 'no')).astype(int)
train_data['loan_housing'] = ((train_data['loan'] == 'no') & (train_data['housing'] == 'no')).astype(int)


train_data['month_group'] = 0
train_data.loc[train_data['month'].isin(['sep', 'oct', 'dec']), 'month_group'] = 1
train_data.loc[train_data['month'].isin(['feb', 'mar', 'apr']), 'month_group'] = 2

In [11]:
test_data['duration500up'] = (test_data['duration'] >= 500).astype(int)
test_data['duration'] = np.log1p(test_data['duration'])
test_data['balance'] = np.log1p(test_data['balance'].apply(lambda x: x + 8020))
test_data['student_default'] = ((test_data['job'] == 'student') & (test_data['default'] == 'no')).astype(int)
test_data['student_loan'] = ((test_data['job'] == 'student') & (test_data['loan'] == 'no')).astype(int)
test_data['student_housing'] = ((test_data['job'] == 'student') & (test_data['housing'] == 'no')).astype(int)
test_data['retired_single'] = ((test_data['job'] == 'retired') & (test_data['marital'] == 'single')).astype(int)
test_data['retired_loan'] = ((test_data['job'] == 'retired') & (test_data['loan'] == 'no')).astype(int)
test_data['single_tertiary'] = ((test_data['marital'] == 'single') & (test_data['education'] == 'tertiary')).astype(int)
test_data['single_default'] = ((test_data['marital'] == 'single') & (test_data['default'] == 'no')).astype(int)
test_data['single_loan'] = ((test_data['marital'] == 'single') & (test_data['loan'] == 'no')).astype(int)
test_data['single_housing'] = ((test_data['marital'] == 'single') & (test_data['housing'] == 'no')).astype(int)
test_data['tertiary_default'] = ((test_data['education'] == 'tertiary') & (test_data['default'] == 'no')).astype(int)
test_data['tertiary_loan'] = ((test_data['education'] == 'tertiary') & (test_data['loan'] == 'no')).astype(int)
test_data['tertiary_housing'] = ((test_data['education'] == 'tertiary') & (test_data['housing'] == 'no')).astype(int)
test_data['default_loan'] = ((test_data['default'] == 'no') & (test_data['loan'] == 'no')).astype(int)
test_data['default_housing'] = ((test_data['default'] == 'no') & (test_data['housing'] == 'no')).astype(int)
test_data['loan_housing'] = ((test_data['loan'] == 'no') & (test_data['housing'] == 'no')).astype(int)

test_data['month_group'] = 0
test_data.loc[test_data['month'].isin(['sep', 'oct', 'dec']), 'month_group'] = 1
test_data.loc[test_data['month'].isin(['feb', 'mar', 'apr']), 'month_group'] = 2

In [12]:
#One-Hot 인코딩, 넘파이 배열 변환
all_data = pd.concat([train_data, test_data], axis=0)
dum=pd.get_dummies(all_data, columns=['job', 'marital', 'education', 'default', 'housing', 'loan', 'contact', 'month', 'poutcome'], drop_first=True)
train_data_final = dum[:len(train_data)]
test_data_final = dum[len(train_data):]
train_data = train_data_final.to_numpy()
train_target = train_target.to_numpy()
test_data = test_data_final.to_numpy()

In [13]:
print(train_data.shape)
print(train_target.shape)
print(test_data.shape)
train_data_final.describe()

(750000, 59)
(750000,)
(250000, 59)


age        balance            day       duration  \
count  750000.000000  750000.000000  750000.000000  750000.000000   
mean       40.926395       9.106751      16.117209       5.064997   
std        10.098829       0.203697       8.250832       1.031530   
min        18.000000       0.693147       1.000000       0.693147   
25%        33.000000       8.989818       9.000000       4.521789   
50%        39.000000       9.065892      17.000000       4.897840   
75%        48.000000       9.149634      21.000000       5.891644   
max        95.000000      11.587458      31.000000       8.500861   

            campaign          pdays       previous  duration500up  \
count  750000.000000  750000.000000  750000.000000  750000.000000   
mean        2.577008      22.412733       0.298545       0.184872   
std         2.718514      77.319998       1.335926       0.388194   
min         1.000000      -1.000000       0.000000       0.000000   
25%         1.000000      -1.000000       0.000000       0.000000   
50%         2.000000      -1.000000       0.000000       0.000000   
75%         3.000000      -1.000000       0.000000       0.000000   
max        63.000000     871.000000     200.000000       1.000000   

       student_default   student_loan  ...  single_default    single_loan  \
count    750000.000000  750000.000000  ...   750000.000000  750000.000000   
mean          0.015657       0.015523  ...        0.255192       0.231029   
std           0.124146       0.123619  ...        0.435969       0.421491   
min           0.000000       0.000000  ...        0.000000       0.000000   
25%           0.000000       0.000000  ...        0.000000       0.000000   
50%           0.000000       0.000000  ...        0.000000       0.000000   
75%           0.000000       0.000000  ...        1.000000       0.000000   
max           1.000000       1.000000  ...        1.000000       1.000000   

       single_housing  tertiary_default  tertiary_loan  tertiary_housing  \
count   750000.000000     750000.000000  750000.000000     750000.000000   
mean         0.123476          0.299047       0.270436          0.167501   
std          0.328983          0.457841       0.444185          0.373423   
min          0.000000          0.000000       0.000000          0.000000   
25%          0.000000          0.000000       0.000000          0.000000   
50%          0.000000          0.000000       0.000000          0.000000   
75%          0.000000          1.000000       1.000000          0.000000   
max          1.000000          1.000000       1.000000          1.000000   

        default_loan  default_housing   loan_housing    month_group  
count  750000.000000    750000.000000  750000.000000  750000.000000  
mean        0.849345         0.444532       0.399460       0.250861  
std         0.357712         0.496914       0.489788       0.643337  
min         0.000000         0.000000       0.000000       0.000000  
25%         1.000000         0.000000       0.000000       0.000000  
50%         1.000000         0.000000       0.000000       0.000000  
75%         1.000000         1.000000       1.000000       0.000000  
max         1.000000         1.000000       1.000000       2.000000  

[8 rows x 24 columns]

## 3. 피처 중요도 확인-수정 반복

In [14]:
from sklearn.model_selection import cross_validate
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import StratifiedKFold
from xgboost import XGBClassifier
sample_weights = np.where(train_data_final['duration500up'] == 1, 2, 1)
#타깃 클래스 편향 방지 scale_pos_weight=7.29
xgb = XGBClassifier(tree_method='hist', device='cuda', eval_metric='auc', max_depth=9,scale_pos_weight=7.29, n_jobs=-1, random_state=42)
cv1 = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [15]:
score = cross_validate(xgb, train_data, train_target, cv = cv1, return_train_score=True, n_jobs=-1)
print(np.mean(score['train_score']), np.mean(score['test_score']))

/usr/local/lib/python3.11/dist-packages/xgboost/core.py:160: UserWarning: [12:06:10] WARNING: /workspace/src/common/error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for booster before call to inplace_predict.

This warning will only be shown once.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.11/dist-packages/xgboost/core.py:160: UserWarning: [12:06:11] WARNING: /workspace/src/common/error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for boo

0.9152006666666667 0.8983639999999999


In [16]:
xgb.fit(train_data, train_target, sample_weight=sample_weights)
feature_names = train_data_final.columns
importances = xgb.feature_importances_
feature_importances = pd.Series(importances, index=feature_names)
print(feature_importances.sort_values(ascending=False))
print(xgb.score(train_data, train_target))

job_student            0.147894
poutcome_success       0.109494
loan_housing           0.108742
duration               0.086198
contact_unknown        0.076236
poutcome_unknown       0.063043
month_group            0.058274
month_mar              0.030307
month_jun              0.024846
month_feb              0.016142
single_loan            0.015778
tertiary_loan          0.012547
month_may              0.010929
job_blue-collar        0.010182
student_housing        0.008786
loan_yes               0.008478
month_jan              0.008036
month_nov              0.007865
tertiary_housing       0.007635
pdays                  0.007358
day                    0.007132
month_oct              0.006792
month_jul              0.006617
default_housing        0.006493
month_aug              0.006346
duration500up          0.006249
month_sep              0.006069
default_loan           0.005915
campaign               0.005860
balance                0.005857
education_tertiary     0.005085
single_d

/usr/local/lib/python3.11/dist-packages/xgboost/core.py:160: UserWarning: [12:06:33] WARNING: /workspace/src/common/error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for booster before call to inplace_predict.

This warning will only be shown once.

  warnings.warn(smsg, UserWarning)


0.9154666666666667


In [17]:
#pd.set_option('display.max_rows', None)
#print(feature_importances.sort_values(ascending=False))

## 4. 모델 학습

In [18]:
param = {
    'n_estimators': [1000, 1200, 1500],
    'max_depth': [7, 8],
    'learning_rate': [0.001, 0.005, 0.01, 0.03],
    'gamma': [0.1, 0.2],
    'reg_lambda': [100, 150, 200],
    'reg_alpha': [0.5, 1],
    'subsample': [0.7, 0.8, 0.9],
    'colsample_bytree': [0.7, 0.8, 0.9]
}

xgb = XGBClassifier(tree_method='hist', device='cuda', eval_metric='auc', scale_pos_weight=7.29, n_jobs=-1, random_state=42)
random_search = RandomizedSearchCV(
    estimator=xgb,
    param_distributions=param,
    n_iter=30,
    random_state=42,
    cv=cv1,
    n_jobs=-1,
)

random_search.fit(train_data, train_target, sample_weight = sample_weights)
model = random_search.best_estimator_

In [22]:
print(random_search.best_params_)
print(model.score(train_data, train_target))
print(random_search.best_score_)

{'subsample': 0.7, 'reg_lambda': 100, 'reg_alpha': 0.5, 'n_estimators': 1500, 'max_depth': 8, 'learning_rate': 0.03, 'gamma': 0.1, 'colsample_bytree': 0.7}
0.901184
0.8956693333333334


In [23]:
 preds_test = model.predict(test_data)

In [25]:
output = pd.DataFrame({'id': test.id,
                       'y': preds_test})
output.to_csv('subfinal.csv', index=False)

## 5. 최종 테스트세트 예측 결과

score: 0.91057  

데이터 셋의 특징에 맞춰서  
1. 파일 불러오기, 정보 보기
2. 전처리(피처 제거, 이상치 제거, 결측치 채우기 등)
3. EDA — 분포· 특성 별 타깃비율·결측 확인+ 타깃 클래스 편향 주의.
4. 기초 파생 특성 만들기
5. 원핫 인코딩
6. Baseline 모델 생성 & CV 점수 기록
7. 피처 중요도 확인 → 낮은 것 제거 or 파생 추가, duration, day/month 등 의심되는 컬럼 제거/추가 비교
8. 하이퍼파라미터 튜닝 (RandomSearch)

순으로 머신러닝 모델을 학습시켜보았다.    
  위 프로젝트를 통해 전반적인 머신러닝 모델링과 피쳐 엔지니어링을 연습할 수 있고, 추후 실험에 이 지식들이 도움이 될것으로 예상한다.  
중요도를 조합하여 피쳐 엔지니어링을 하였지만, 대회 상위권인 테스트 셋 정확도 96% 이상의 점수는 얻지 못하였다.  
이는 데이터 셋의 기본 구조, 도메인 지식, 파생 피쳐 생성 등에 대해 이해가 부족했던 것으로 예상한다.  
앞으로 데이터사이언스를 배우면서 이 과정들에 대해 보다 전문적인 공부가 필요함을 알 수 있었다.  